In [1]:
import os
import folium
import pandas as pd
import numpy as np
import networkx as nx
from haversine import haversine

In [2]:
nodes = pd.read_csv('data/Jeju_nodes.csv', encoding='utf-8')
links = pd.read_csv('data/Jeju_links.csv', encoding='cp949')
car = pd.read_csv('data/Jeju_car.csv', encoding='cp949')

nodes = nodes[['Id','NODE_NAME','latitude','longitude']]
links = links[['Source','Target', '시간']]
source_in = links['Source'].apply(lambda x : x in list(nodes['Id'])) # check Sources are in jeju
target_in = links['Target'].apply(lambda x : x in list(nodes['Id'])) # check Targets are in jeju
# source_in and target_in are boolean type pandas.Series which contains True or False
jeju_links = links[source_in & target_in] # contain if both target and source are contained in jeju

In [3]:
G = nx.Graph()
# R is the Earth's radius
R = 6371e3

for idx,row in nodes.iterrows():
    # add node to Graph G
    G.add_node(row['Id'],Label=row['NODE_NAME'],latitude=row['latitude'], longitude=row['longitude'])

for idx,row in jeju_links.iterrows():
    # Link attribute : 'Source', 'Target' and weight = '시간 between two nodes'
    G.add_edge(row['Source'],row['Target'],weight = row['시간'])

In [4]:
def connectRes(graph, df): # df는 idx, latitude, longitude가 있어야함
    nodes_latitude = nx.get_node_attributes(graph, 'latitude')
    nodes_longitude = nx.get_node_attributes(graph, 'longitude')
    for idx, row in df.iterrows():
        distances ={}
        for keyLong, valLat in nodes_latitude.items():
            nodesPos = (valLat, nodes_longitude[keyLong])
            curPos = (row['latitude'], row['longitude'])
            distances[keyLong] = haversine(nodesPos, curPos, unit='km')
        nearest_node = min(distances, key=distances.get)
        graph.add_node(idx, Label=idx, latitude=row['latitude'], longitude=row['longitude']) ##노드이름은 4050000000이하로 설정
        w = distances[nearest_node]*1000/666 #단위 변환 km->m(*1000), 거리(m)->시간(분) (40km/h = 666m/s)
        graph.add_edge(nearest_node, idx, weight=w) 
    return graph

G = connectRes(G, car)
print(f"Data: {len(car)}, Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")

Data: 31, Nodes: 4249, Edges: 6046


In [5]:
def propagation(G, start_node, w = 5):
    shortest_paths = nx.single_source_dijkstra_path_length(G, start_node, cutoff=w, weight='weight')
    # print(f"Start node: {start_node}")
    # print(f"Number of selected Node: {len(shortest_paths)}")
    return shortest_paths

def mergeDict(dict1, dict2):
    result_dict = {}

# Iterate over keys present in both dictionaries
    for key in set(dict1.keys()).intersection(dict2.keys()):
        # Choose the smaller value
        result_dict[key] = min(dict1[key], dict2[key])

    # Add keys from the first dictionary that are not in the second dictionary
    result_dict.update({key: dict1[key] for key in set(dict1.keys()) - set(dict2.keys())})

    # Add keys from the second dictionary that are not in the first dictionary
    result_dict.update({key: dict2[key] for key in set(dict2.keys()) - set(dict1.keys())})

    return result_dict

serviceArea = {}
for idx, row in car.iterrows():
    tmp = propagation(G, idx, w=5)
    serviceArea = mergeDict(serviceArea, tmp)

print(serviceArea)


{4050137600.0: 3.0124831069556848, 4050124800.0: 3.9071372995556852, 4050133000.0: 2.000469689555685, 4050137100.0: 3.7203990079556846, 4050141200.0: 3.4588515845556853, 4050132500.0: 2.077961408755685, 4050081300.0: 3.5003777575556856, 24: 0, 4050136600.0: 3.115707729955685, 30: 0, 4050132000.0: 3.651690115055685, 4050131500.0: 3.304670167555684, 4050135600.0: 2.3540314475556854, 4050139700.0: 3.158166341555685, 4050131000.0: 3.2144170038556843, 4050135100.0: 2.8052529545556855, 4050139200.0: 4.886049596555685, 4050130500.0: 1.6697952445556852, 4050134600.0: 2.928783510755685, 4050138700.0: 2.7688406555556853, 4050142800.0: 4.690449995555685, 4050134100.0: 2.669876602755685, 4050129500.0: 3.2011576145556853, 4050142300.0: 4.639689084055685, 4050133600.0: 3.4716047125556857, 4050137700.0: 2.235619857955685, 4050133100.0: 1.1851502035556851, 4050137200.0: 3.5025555299556848, 4050128500.0: 3.1084663035556854, 4050132600.0: 3.694616135655685, 4050081400.0: 3.8957549639556848, 4050140800.0

In [22]:
# 제주도 가운데
std_point = (33.37283976160554, 126.5439861097205 )

In [41]:
map_osm = folium.Map(location=std_point, zoom_start=10) 

kw = {'opacity': 0.5, 'weight': 2}
for edge in G.edges(data=True):
    source, target, attributes = edge

    # Check if the source and target nodes exist in the graph
    if source in G.nodes and target in G.nodes:
        start = tuple([G.nodes[source]['latitude'], G.nodes[source]['longitude']])
        end = tuple([G.nodes[target]['latitude'], G.nodes[target]['longitude']])

        folium.PolyLine(
            locations=[start, end],
            color='blue',
            line_cap='round',
            **kw,
        ).add_to(map_osm)
    else:
        print(source, target)

for key, val in serviceArea.items():
    row = nodes.loc[nodes['Id'] == key]
    try:
        location = (row['latitude'].values[0], row['longitude'].values[0]) # 위도, 경도 튜플
    except:
        # print(row, key)
        pass

    folium.Circle(
        location=location,
        radius=500, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='red',
        fill=True,  # gets overridden by fill_color
        # popup=str(row['Id'])
    ).add_to(map_osm)

for ix, row in car.iterrows():
    location = (row['latitude'], row['longitude']) # 위도, 경도 튜플
    folium.Circle(
        location=location,
        radius=1000, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='black',
        fill=True,  # gets overridden by fill_color
        # popup=str(row['Id'])
    ).add_to(map_osm)
    
map_osm